# Coder une variable aléatoire

Marc Lorenzi - 9 juin 2018

In [ ]:
from math import sqrt
from fractions import Fraction

Dans ce notebook nous allons mettre en place quelques fonctions permettant de coder simplement et élégamment la loi d'une variable aléatoire. Nous verrons que notre codage s'adapte immédiatement à la représentation d'un couple de variables aléatoires et permet de calculer facilement espérance, variance, covariance et tout un tas d'autres choses.

Un autre titre pour ce notebook pourrait être : __dictionnaires__.

## 1. Coder la loi d'une variable aléatoire

Pour coder la loi d'une variable aléatoire $X$ (prenant un nombre fini de valeurs, cela va de soi), nous allons utiliser un __dictionnaire__ que nous noterons comme la variable aléatoire, $X$. Bref, nous oublierons l'ensemble de départ de $X$ pour ne garder que sa loi. Les clés du dictionnaire sont les valeurs prises par $X$ et pour toute clé $x$, $X[x]=P[X=x]$.

Nous allons coder les lois usuelles dans la suite de cette section.

### 1.1 Loi de Bernoulli

Commençons par la loi de Bernoulli de paramètre $p\in[0,1]$.

In [ ]:
def Bernoulli(p):
    return {0:1-p, 1:p}

In [ ]:
Bernoulli(Fraction(1,3))

### 1.2 Les dictionnaires en Python

La structure de dictionnaire permet d'associer des __valeurs__ à des objets, les __clés__ du dictionnaire. Les clés peuvent être à peu près n'importe quoi (ce n'est pas tout à fait vrai mais n'entrons pas dans les détails), les valeurs aussi.

Quelques fonctions permettent de travailler avec les dictionnaires. Nous venons de voir comment en initialiser un dans la fonction `Bernoulli`. Si $d$ est un dictionnaire, voici quelques méthodes associées :

- Obtenir la valeur associée à une clé $k$ : `d[k]`
- Associer à la clé $k$ la valeur $v$ : `d[k]=v`
- Le dictionnaire $d$ a-t-il la clé $k$ ? `k in d`
- Supprimer la clé $k$ : `del d[k]`
- Itérer sur l'ensemble des clés : `for k in d ...`

Les trois méthodes ci-dessous renvoient des objets de type `view`. Je ne précise pas plus avant.

- Obtenir toutes les clés : `d.keys()`. Une instruction du type `list(d.keys())` renvoie la liste des clés.
- Obtenir toutes les valeurs : `d.values()`
- Obtenir tous les couples (clé, valeur) : `d.items()`

et encore bien d'autres méthodes. Consultez la documentation de Python.

En exemple, voici en une ligne l'ensemble des valeurs prises par une variable aléatoire codée avec notre modèle :

In [ ]:
def valeurs_prises(X):
    return list(X.keys())

In [ ]:
valeurs_prises(Bernoulli(Fraction(1, 3)))

Et voici une fonction qui vérifie si une variable aléatoire en est bien une.

In [ ]:
def est_va(X):
    s = 0
    for x in X:
        if X[x] < 0 or X[x] > 1: return False
        s = s + X[x]
    return s == 1

In [ ]:
est_va(Bernoulli(Fraction(1,3)))

### 1.3 Fonctions utiles

Avant de passer aux lois binomiale et hypergéométrique, définissons quelques fonctions bien utiles.

La fonction `power_dn` prend en paramètres deux entiers $n$ et $k$ et renvoie $(n)_k=n(n-1)\ldots(n-k+1)$.

In [ ]:
def power_dn(n, k):
    p = 1
    for i in range(k):
        p = p * (n - i)
    return p

In [ ]:
power_dn(6, 3)

La fonction `factorial` calcule ... la factorielle de l'entier $n$.

In [ ]:
def factorial(n):
    return power_dn(n, n)

In [ ]:
factorial(10)

Et enfin, la fonction `binom` prend deux entiers $n$ et $k$ en paramètres et renvoie le coefficient binomial $\binom n k$.

In [ ]:
def binom(n, k):
    return power_dn(n, k) // factorial(k)

In [ ]:
binom(6, 3)

Remarquons que cette fonction marché très bien même si $k > n$ :

In [ ]:
binom(5, 12)

### 1.4 La loi binomiale

La fonction `Binomial` prend en paramètres un entier $n$ et un réel $p\in[0,1]$  et renvoie (la loi d') une variable aléatoire suivant la loi binomiale $\mathcal B(n, p)$. Dans la suite j'abuserai et j'identifierai la variable aléatoire et sa loi.

In [ ]:
def Binomial(n, p):
    X = {}
    for k in range(n + 1):
        X[k] = binom(n, k) * p ** k * (1 - p) ** (n - k)
    return X

In [ ]:
Binomial(5, Fraction(1, 4))

In [ ]:
est_va(_)

### 1.5 La loi hypergéométrique

Soient $r,n,N$ trois entiers tels que $r,n\le N$. La loi hypergéométrique de paramètres $r, n, N$ est définie ainsi :   pour $0\le k\le n$,
$$P(X=k)=\frac{\binom r k \binom {N-r}{n-k}}{\binom N n}$$

In [ ]:
def Hypergeom(r, n, N):
    X = {}
    for k in range(n + 1):
        X[k] = Fraction(binom(r, k) * binom(N - r, n - k), binom(N, n))
    return X

__Exemple__ : une urne contient $N=20$ boules. Parmi celles-ci, $r=8$ boules sont rouges. On tire $n=10$ boules dans l'urne __sans remise__. Soit $X$ le nombre de boules rouges tirées. Alors $X$ suit une loi hypergéométrique $\mathcal H(r,n,N)$.

In [ ]:
Hypergeom(8, 10, 20)

Remarquez que les événements $\{X=9\}$ et $\{X=10\}$ sont de probabilité nulle, ce qui est heureux puisqu'ils sont vides.

In [ ]:
est_va(_)

## 2. Espérance, variance

### 2.1 Formule de transfert

Au lieu de réécrire plusieurs fois la même chose, codons une fonction très générale `gen_esp`. Cette fonction prend en paramètres une fonction $f:\mathbb R\to\mathbb R$ et une variable aléatoire réelle $X$. Elle renvoie $E(f(X))$, l'espérance de la variable aléatoire $f(X)$.

Comment ? Eh bien mettons que $X:\Omega\to\mathbb R$. Le théorème de transfert nous dit que

$$E(f(X))=\sum_{x\in X(\Omega)}f(x)P(X=x)$$

La fonction `gen_esp` est donc facile à écrire.

In [ ]:
def gen_esp(f, X):
    s = 0
    for x in X:
        s = s + f(x) * X[x]
    return s

In [ ]:
gen_esp(lambda x:  x ** 2, Binomial(5, Fraction(1, 3)))

### 2.2 Moments d'une variable aléatoire réelle

__Définition__ : Pour tout entier $n\in\mathbb N$, le moment d'ordre $n$ de la variable aléatoire $X$ est l'espérance de $X^n$ :

In [ ]:
def moment(X, n):
    return gen_esp(lambda x: x ** n, X)

In [ ]:
moment(Binomial(5, Fraction(1, 3)), 2)

### 2.3 Espérance

L'espérance est donc le moment d'ordre 1 !

In [ ]:
def esperance(X):
    return moment(X, 1)

In [ ]:
esperance(Binomial(5, Fraction(1, 3)))

On retrouve le résultat bien connu. Si $X$ suit une loi binomiale $\mathcal B(n,p)$, alors $E(X)=np$.

In [ ]:
esperance(Hypergeom(8, 10, 20))

On retrouve le résultat moins bien connu. Si $X$ suit une loi hypergéométrique $\mathcal H(r, n, N)$, alors $E(X)=\frac {nr} N$.

### 2.4 Variance

Et voici en une ligne la variance.

In [ ]:
def variance(X):
    return moment(X, 2) - esperance(X) ** 2

In [ ]:
variance(Binomial(5, Fraction(1, 3)))

Le résultat général pour la loi binomiale $\mathcal B(n,p)$ est $V(X)=np(1-p)$.

In [ ]:
variance(Hypergeom(8, 10, 20))

Le résultat général pour la loi hypergéométrique $\mathcal H(r,n,H)$ est $V(X)=np(1-p)\frac{N-n}{N-1}$ où $p=\frac r N$.

In [ ]:
p = Fraction(8, 20)
10 * p * (1 - p) * Fraction(20 - 10, 20 - 1)

On a bien sûr pour pas cher l'écart-type d'une variable aléatoire.

In [ ]:
def ecart_type(X):
    return sqrt(variance(X))

__Exercice__ : Le __moment centré__ d'ordre $n$ d'une variable aléatoire réelle est $M_n(X)=E(X-E(X))^n$. Écrire une fonction `moment_centré(X, n)`.

## 3. Couples de variables aléatoires

Comment coder un couple de variables aléatoires ? Mais dans un dictionnaire bien entendu ! Sauf que cette fois-ci, les clés du dictionnaire sont des couples.

### 3.1 L'exemple

Nous allons travailler sur l'exemple de la loi du couple $(X,Y)$ où $X$ est l'ordre d'une permutation de $\mathfrak S_6$ et $Y$ est le nombre d'orbites non triviales de la permutation. Il nous faut d'abord trouver la loi conjointe. Pour cela, listons toutes les permutations de $\mathfrak S_6$ (il y en a $6!=720$) par la nature de leur décomposition en produit de cycles de supports disjoints. Dans l'ordre ci-dessous : le type de permutation, entre parenthèses le nombre de telles permutations, puis leur ordre et leur nombre d'orbites.

- $id$ : $(1)\ 1, 0$
- $(ij)$ : $(15)\ 2, 1$
- $(ijk)$ : $(40)\ 3, 1$
- $(ijkl)$ : $(90)\ 4, 1$
- $(ijklm)$ : $(144)\ 5, 1$
- $(ijklmn)$ : $(120)\ 6, 1$
- $(ij)(kl)$ : $(45)\ 2, 2$
- $(ij)(kl)(mn)$ : $(15)\ 2, 3$
- $(ijk)(lm)$ : $(120)\ 6, 2$
- $(ijk)(lmn)$ : $(40)\ 3, 2$
- $(ijkl)(mn)$ : $(90)\ 4, 2$

Au lecteur le soin de vérifier tous ces chiffres. C'est un excellent exercice.

In [ ]:
XY = {
    (1,0): Fraction(1, 720),
    (2,1): Fraction(15, 720),
    (3,1): Fraction(40, 720),
    (4,1): Fraction(90, 720),
    (5,1): Fraction(144, 720),
    (6,1): Fraction(120, 720),
    (2,2): Fraction(45, 720),
    (2,3): Fraction(15, 720),
    (6,2): Fraction(120, 720),
    (3,2): Fraction(40, 720),
    (4,2): Fraction(90, 720)
    
}

### 3.2 Lois marginales

Soit $Z=(X, Y)$ un couple de variables aléatoires réelles. Connaissant la loi de $Z$, commet calculer la loi de $X$ ? 

Il suffit de sommer sur les valeurs prises par $Y$ : 

$$P(X=x)=\sum_y P(X=x, Y=y)$$

où $y$ varie dans l'ensemble des valeurs prises par $Y$. On obtient évidemment, en sommant sur $x$, la loi de $Y$. La fonction `loi_marginale` fait le travail. Elle prend un paramètre $Z$ (représentant un couple $(X, Y)$ de variables aléatoires) et un entier $j$ qui vaut 0 ou 1. Si $j=0$ la fonction renvoie la loi de $X$. Si $j=1$ elle renvoie la loi de $Y$. 

In [ ]:
def loi_marginale(Z, j):
    X = {}
    for t in Z:
        x = t[j]
        if x in X: X[x] = X[x] + Z[t]
        else: X[x] = Z[t]
    return X

Reprenons notre exemple fétiche.

In [ ]:
X = loi_marginale(XY, 0)
print(X)

In [ ]:
Y = loi_marginale(XY, 1)
print(Y)

Petite vérification ?

In [ ]:
est_va(X), est_va(Y)

Tout va bien. Au passage :

In [ ]:
print(esperance(X), variance(X))
print(esperance(Y), variance(Y))

### 3.2 Covariance

Étant données deux variables aléatoires $X$ et $Y$, leur covariance est $Cov(X, Y)=E(XY)-E(X)E(Y)$. Avec un peu de réflexion on se rend compte que pour calculer $E(XY)$ il suffit d'utiliser la fonction `gen_esp` que nous avons déjà vue, sauf que maintenant la fonction $f$ est une "fonction de deux variables" ! Bref, tout est déjà écrit, il suffit de recoller les morceaux.

In [ ]:
def covariance(Z):
    EX = esperance(loi_marginale(Z, 0))
    EY = esperance(loi_marginale(Z, 1))
    EXY = gen_esp(lambda z: z[0] * z[1], Z)
    return EXY - EX * EY

In [ ]:
covariance(XY)

In [ ]:
float(_)

In [ ]:
print(ecart_type(X) * ecart_type(Y))

Pourquoi ce dernier calcul ? Rappelons-nous : étant données deux variables aléatoires $X$ et $Y$ on a $|Cov(X,Y)|\le\sigma(X)\sigma(Y)$, le produit de leurs écarts-types. Si $X$ et $Y$ ont des écarts-types non nuls, on pose
$$\rho(X,Y)=\frac{Cov(X,Y)}{\sigma(X)\sigma(Y)}$$

__Proposition__ : 

- $-1\le\rho(X,Y)\le 1$
- $\rho(X,Y)=\pm 1$ si et seulement si il existe trois réels $a, b, c$, $(a,b)\ne(0,0)$ tels que $aX+bY+c=0$ presque sûrement.
- Si $X$ et $Y$ sont indépendantes, $\rho(X,Y)=0$.

__Démonstration__ : faite en cours.

__Définition__ $\rho(X, Y)$ est le coefficient de corrélation des variables $X$ et $Y$.

In [ ]:
def correlation(Z):
    X = loi_marginale(Z, 0)
    Y = loi_marginale(Z, 1)
    return covariance(Z) / (ecart_type(X) * ecart_type(Y))

Et pour finir, le coefficient de corrélation de la signature et de l'ordre dans $\mathfrak S_5$.

In [ ]:
correlation(XY)

Que signifie cette valeur ? Traçons les couples $(x,y)$ des valeurs prises par le couple $(X,Y)$.

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
sx = [x for (x,y) in XY]
sy = [y for (x,y) in XY]
plt.plot(sx, sy, 'o')
plt.grid()
plt.show()

si notre coefficient de corrélation était $\pm 1$, les points seraient alignés. Un coefficient de 0 indiquerait des points "un peu n'importe comment". Ici, je n'ose rien dire :-).

__Mini projet__ : automatiser tout cela dans $\mathfrak S_n$ (avec $n$ quelconque mais raisonnable, cela va de soi). Voici un plan possible :

- Écrire une fonction qui calcule toutes les permutations de $\mathfrak S_n$.
- Utiliser pour le reste des étapes les fonctions qui ont été écrites dans le notebook dédié aux permutations.